<a href="https://colab.research.google.com/github/bachaudhry/kaggle-cmi-detect-behavior/blob/main/notebooks/05B_Hyper_Parameter_Tuning_CMI_Detect_Behavior.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [2]:
from google.colab import drive
drive.mount('/content/drive')

#import os
#os.environ["KAGGLE_CONFIG_DIR"] = "/content/drive/MyDrive/Kaggle"

Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).


In [3]:
import sys
sys.path.append('/content/drive/MyDrive/Kaggle/CMI - Hyperparameter Tuning/')

In [4]:
!! pip install catboost optuna wandb

['Requirement already satisfied: catboost in /usr/local/lib/python3.12/dist-packages (1.2.8)',
 'Requirement already satisfied: optuna in /usr/local/lib/python3.12/dist-packages (4.5.0)',
 'Requirement already satisfied: wandb in /usr/local/lib/python3.12/dist-packages (0.21.1)',
 'Requirement already satisfied: graphviz in /usr/local/lib/python3.12/dist-packages (from catboost) (0.21)',
 'Requirement already satisfied: matplotlib in /usr/local/lib/python3.12/dist-packages (from catboost) (3.10.0)',
 'Requirement already satisfied: numpy<3.0,>=1.16.0 in /usr/local/lib/python3.12/dist-packages (from catboost) (2.0.2)',
 'Requirement already satisfied: pandas>=0.24 in /usr/local/lib/python3.12/dist-packages (from catboost) (2.2.2)',
 'Requirement already satisfied: scipy in /usr/local/lib/python3.12/dist-packages (from catboost) (1.16.1)',
 'Requirement already satisfied: plotly in /usr/local/lib/python3.12/dist-packages (from catboost) (5.24.1)',
 'Requirement already satisfied: six in 

In [5]:
import pandas as pd
import numpy as np
import os
import catboost as cat
from sklearn.model_selection import StratifiedGroupKFold
from sklearn.metrics import f1_score, make_scorer
from sklearn.inspection import permutation_importance
from sklearn.decomposition import PCA
import matplotlib.pyplot as plt
import seaborn as sns
import optuna
import warnings
from functools import partial
import pickle
import time

warnings.filterwarnings('ignore')
pd.set_option('display.max_columns', None)
sns.set_style('whitegrid')

# --- Pathing and Experiment Tracking Setup ---
from src.tracking import ExperimentTracker
from src.config import USE_WANDB, WANDB_PROJECT, WANDB_ENTITY, PROJECT_PATH
from src.feature_engineering import create_wave2_features, create_wave3_features, create_wave4_features, create_wave5_features

tracker = ExperimentTracker(
    project_path=PROJECT_PATH,
    use_wandb=USE_WANDB,
    wandb_project_name=WANDB_PROJECT,
    wandb_entity=WANDB_ENTITY
)

SEED = 42
N_TRIALS = 75
HOLDOUT_SPLIT_INDEX = 0 # Which fold from Stratified Group K-fold to use as a holdout


In [6]:
def display_all(df):
    with pd.option_context("display.max_rows", 10000, "display.max_columns", 10000):
        display(df)

In [7]:
DATA_PATH = '/content/drive/MyDrive/Kaggle/CMI - Hyperparameter Tuning/data'
MAPPING_PATH = '/content/drive/MyDrive/Kaggle/CMI - Hyperparameter Tuning/processed_data/'

In [8]:
# Load full training data, gesture mappings and inverse gesture mappings
#df_train = pd.read_feather('processed_data/train_full.feather')
df_train = pd.read_csv(os.path.join(DATA_PATH, 'train.csv'))
df_demographics = pd.read_csv(os.path.join(DATA_PATH, 'train_demographics.csv'))

with open(MAPPING_PATH + 'gesture_mappings.pkl', 'rb') as f:
    gesture_to_seq_type_map, gesture_map, inv_gesture_map = pickle.load(f)

In [9]:
display_all(df_train.head(5))

row_id sequence_type sequence_id  sequence_counter      subject  \
0  SEQ_000007_000000        Target  SEQ_000007                 0  SUBJ_059520   
1  SEQ_000007_000001        Target  SEQ_000007                 1  SUBJ_059520   
2  SEQ_000007_000002        Target  SEQ_000007                 2  SUBJ_059520   
3  SEQ_000007_000003        Target  SEQ_000007                 3  SUBJ_059520   
4  SEQ_000007_000004        Target  SEQ_000007                 4  SUBJ_059520   

                       orientation                                   behavior  \
0  Seated Lean Non Dom - FACE DOWN  Relaxes and moves hand to target location   
1  Seated Lean Non Dom - FACE DOWN  Relaxes and moves hand to target location   
2  Seated Lean Non Dom - FACE DOWN  Relaxes and moves hand to target location   
3  Seated Lean Non Dom - FACE DOWN  Relaxes and moves hand to target location   
4  Seated Lean Non Dom - FACE DOWN  Relaxes and moves hand to target location   

        phase             gesture     acc_x     acc_y     acc_z     rot_w  \
0  Transition  Cheek - pinch skin  6.683594  6.214844  3.355469  0.134399   
1  Transition  Cheek - pinch skin  6.949219  6.214844  3.125000  0.143494   
2  Transition  Cheek - pinch skin  5.722656  5.410156  5.421875  0.219055   
3  Transition  Cheek - pinch skin  6.601562  3.531250  6.457031  0.297546   
4  Transition  Cheek - pinch skin  5.566406  0.277344  9.632812  0.333557   

      rot_x     rot_y     rot_z      thm_1      thm_2      thm_3      thm_4  \
0 -0.355164 -0.447327 -0.809753  28.943842  31.822186  29.553024  28.592863   
1 -0.340271 -0.428650 -0.824524  29.340816  31.874645  29.791740  28.663383   
2 -0.274231 -0.356934 -0.865662  30.339359  30.935045  30.090014  28.796087   
3 -0.264160 -0.238159 -0.885986  30.543730  27.044001  29.310717  29.018711   
4 -0.218628 -0.063538 -0.914856  29.317265  25.270855  26.808746  29.408604   

       thm_5  tof_1_v0  tof_1_v1  tof_1_v2  tof_1_v3  tof_1_v4  tof_1_v5  \
0  28.310535     131.0     134.0     132.0     135.0      98.0      74.0   
1  28.406172     130.0     138.0     131.0     135.0     101.0      76.0   
2  28.529778     137.0     136.0     147.0     109.0      90.0      81.0   
3  27.402010     143.0     147.0     170.0     127.0     109.0      98.0   
4  27.357603     178.0     191.0     183.0     157.0     146.0     139.0   

   tof_1_v6  tof_1_v7  tof_1_v8  tof_1_v9  tof_1_v10  tof_1_v11  tof_1_v12  \
0      64.0      60.0      -1.0      -1.0      152.0      153.0      141.0   
1      66.0      61.0      -1.0      -1.0      156.0      155.0      141.0   
2      74.0      74.0      -1.0     164.0      165.0      146.0      106.0   
3      95.0      95.0      -1.0     177.0      189.0      177.0      136.0   
4     143.0     148.0      -1.0      -1.0      236.0      238.0      208.0   

   tof_1_v13  tof_1_v14  tof_1_v15  tof_1_v16  tof_1_v17  tof_1_v18  \
0       89.0       68.0       63.0       -1.0       -1.0       -1.0   
1       93.0       74.0       64.0       -1.0       -1.0       -1.0   
2       94.0       77.0       77.0       -1.0       -1.0       -1.0   
3      121.0      107.0      104.0       -1.0       -1.0       -1.0   
4      200.0      185.0      190.0       -1.0       -1.0       -1.0   

   tof_1_v19  tof_1_v20  tof_1_v21  tof_1_v22  tof_1_v23  tof_1_v24  \
0       -1.0      169.0      118.0       86.0       73.0       -1.0   
1       -1.0      165.0      116.0       86.0       75.0      130.0   
2      180.0      140.0      118.0      103.0       92.0       -1.0   
3      202.0      171.0      160.0      141.0      135.0       -1.0   
4      210.0      246.0      225.0      228.0      202.0      149.0   

   tof_1_v25  tof_1_v26  tof_1_v27  tof_1_v28  tof_1_v29  tof_1_v30  \
0       -1.0       -1.0       -1.0       -1.0      147.0      110.0   
1       -1.0       -1.0       -1.0       -1.0      142.0      114.0   
2       -1.0       -1.0       -1.0       -1.0      155.0      119.0   
3       -1.0       -1.0       -1.0    

In [10]:
print(f"Gesture Map: {gesture_map}")
print(f"\nInverted Gesture Map: {inv_gesture_map}")
print(f"\nGesture To Sequence Type: {gesture_to_seq_type_map}")

Gesture Map: {'Cheek - pinch skin': 0, 'Forehead - pull hairline': 1, 'Write name on leg': 2, 'Feel around in tray and pull out an object': 3, 'Neck - scratch': 4, 'Neck - pinch skin': 5, 'Eyelash - pull hair': 6, 'Eyebrow - pull hair': 7, 'Forehead - scratch': 8, 'Above ear - pull hair': 9, 'Wave hello': 10, 'Write name in air': 11, 'Text on phone': 12, 'Pull air toward your face': 13, 'Pinch knee/leg skin': 14, 'Scratch knee/leg skin': 15, 'Drink from bottle/cup': 16, 'Glasses on/off': 17}

Inverted Gesture Map: {0: 'Cheek - pinch skin', 1: 'Forehead - pull hairline', 2: 'Write name on leg', 3: 'Feel around in tray and pull out an object', 4: 'Neck - scratch', 5: 'Neck - pinch skin', 6: 'Eyelash - pull hair', 7: 'Eyebrow - pull hair', 8: 'Forehead - scratch', 9: 'Above ear - pull hair', 10: 'Wave hello', 11: 'Write name in air', 12: 'Text on phone', 13: 'Pull air toward your face', 14: 'Pinch knee/leg skin', 15: 'Scratch knee/leg skin', 16: 'Drink from bottle/cup', 17: 'Glasses on/of

## Feature Engineering and Hyper Parameter Tuning on a Single Fold.

In [11]:
# Create wave 5 features
features_df_wave5 = create_wave5_features(df_train, df_demographics)


features_df_wave5.head()

Starting Wave 5 Feature Engineering (Temporal Features)...
 Raw sensor DataFrame shape: (574945, 341)
 Generating Wave 4 features (includes Waves 1, 2, 3)...
Starting Wave 4 Feature Engineering (Interaction & Demographics on Aggregated Features)...
 Raw sensor DataFrame shape: (574945, 341)
 Demographics DataFrame shape: (81, 8)
 Unique subjects in sensor data: 81
 Unique subjects in demographics data: 81
 Generating Wave 3 features (includes Waves 1, 2)...
Starting Wave 3 Feature Engineering (ToF PCA - Raw Data Approach)...
 Raw input DataFrame shape: (574945, 341)
 Preparing raw ToF data for PCA...
  - Found 320 ToF columns for PCA.
  - Handling -1.0 values in ToF data...
  - Replaced 105770214 instances of -1.0 with NaN in ToF data for PCA.
 Applying PCA to raw ToF data (n_components=50)...
  - Found 109292646 NaN values in raw ToF data. Imputing with 0...
  - PCA completed. Transformed data shape: (574945, 50)
 Adding PCA components to raw dataframe...
  - Raw dataframe with PCA co

acc_x_mean_Gesture  acc_x_mean_Transition  acc_x_std_Gesture  \
sequence_id                                                                 
SEQ_000007             6.875854               5.227969           0.779424   
SEQ_000008             3.449929               3.353906           0.736728   
SEQ_000013            -7.591276              -6.364640           1.143683   
SEQ_000016             5.291590               5.818142           0.940102   
SEQ_000018             6.235639               3.881445           0.241211   

             acc_x_std_Transition  acc_x_min_Gesture  acc_x_min_Transition  \
sequence_id                                                                  
SEQ_000007               1.334370           5.492188              3.613281   
SEQ_000008               1.346681           1.734375              1.886719   
SEQ_000013               1.162073          -9.250000             -7.714844   
SEQ_000016               1.174814           3.859375              3.437500   
SEQ_000018               1.901476           5.718750              1.964844   

             acc_x_max_Gesture  acc_x_max_Transition  acc_x_median_Gesture  \
sequence_id                                                                  
SEQ_000007            9.015625              7.292969              6.964844   
SEQ_000008            4.949219              5.906250              3.457031   
SEQ_000013           -5.226562             -3.347656             -8.007812   
SEQ_000016            9.378906              7.925781              5.277344   
SEQ_000018            6.832031              6.332031              6.232422   

             acc_x_median_Transition  acc_x_skew_Gesture  \
sequence_id                                                
SEQ_000007                  5.070312            0.671795   
SEQ_000008                  2.691406           -0.292417   
SEQ_000013                 -6.582031            0.395099   
SEQ_000016                  6.578125            2.323306   
SEQ_000018                  2.921875            0.194196   

             acc_x_skew_Transition  acc_y_mean_Gesture  acc_y_mean_Transition  \
sequence_id                                                                     
SEQ_000007                0.119323            5.640137               1.708125   
SEQ_000008                0.278393            7.261364               3.472433   
SEQ_000013                1.138648            3.751562               0.513077   
SEQ_000016               -0.451960           -4.744830              -3.984954   
SEQ_000018                0.300721            6.068704               0.779492   

             acc_y_std_Gesture  acc_y_std_Transition  acc_y_min_Gesture  \
sequence_id                                                               
SEQ_000007            0.582177              3.493182           4.683594   
SEQ_000008            0.824113              3.638059           4.718750   
SEQ_000013            0.571292              2.984959           2.656250   
SEQ_000016            0.441674              0.494274          -5.718750   
SEQ_000018            0.211266              4.005993           5.566406   

             acc_y_min_Transition  acc_y_max_Gesture  acc_y_max_Transition  \
sequence_id                                                                  
SEQ_000007              -2.019531           6.519531              6.214844   
SEQ_000008              -0.222656           8.667969              7.976562   
SEQ_000013              -3.273438           4.683594              3.957031   
SEQ_000016              -4.875000          -3.113281             -2.960938   
SEQ_000018              -3.164062           6.449219              6.718750   

             acc_y_median_Gesture  acc_y_median_Transition  \
sequence_id                                                  
SEQ_000007               5.621094                 0.277344   
SEQ_000008               7.398438                 0.546875   
SEQ_000013               3.746094                 1.695312   
SEQ_000

Action Plan to Accelerate Tuning

1. Switch to a Fixed Hold-Out Validation Set:

    The Problem: Full CV per trial is too slow.

    The Solution: Instead of re-splitting the data 5 times for every trial, we will perform one single split at the very beginning. We will create a large training set (~80% of the data) and a single, fixed hold-out validation set (~20%).

    The Process: Inside each Optuna trial, the model will train once on the large training set and evaluate once on the hold-out set. This immediately gives us a 5x speedup.

2. Re-introduce GPU Acceleration:

    The Problem: Training on the CPU is still time-consuming for each model fit.

    The Solution: This is the perfect time to leverage your RTX 4080. CatBoost has excellent GPU support. By simply adding task_type: 'GPU' to the model parameters, we can expect another significant speedup on top of the hold-out strategy.

Combined Impact: The 5x speedup from the hold-out set, combined with a potential 2-5x speedup from the GPU, will bring the total tuning time from ~83 hours down to a much more manageable 2-8 hours, well within your 12-hour target.




In [12]:
# --- Create a Single, Fixed Hold-Out Validation Set ---

# Prepare your data
feature_cols = [col for col in features_df_wave5.columns if col not in ['subject', 'gesture', 'gesture_encoded']]
X_full = features_df_wave5[feature_cols]
y_full = features_df_wave5['gesture_encoded']
groups_full = features_df_wave5['subject']

In [13]:
#Create a Single, Fixed Hold-Out Validation Set --
print("Splitting data into a single train/validation set for rapid tuning...")

# Use StratifiedGroupKFold to ensure the split is representative and respects groups
# We take one specific fold (e.g., the first) as our hold-out set.
cv_splitter = StratifiedGroupKFold(n_splits=5, shuffle=True, random_state=SEED)

# Get the first split (or the one specified by HOLDOUT_SPLIT_INDEX)
splits = cv_splitter.split(X_full, y_full, groups_full)

# Advance the iterator to the desired fold index
for i in range(HOLDOUT_SPLIT_INDEX + 1):
    train_idx, val_idx = next(splits)

# Perform the actual split
X_train_holdout = X_full.iloc[train_idx]
y_train_holdout = y_full.iloc[train_idx]
X_val_holdout = X_full.iloc[val_idx]
y_val_holdout = y_full.iloc[val_idx]
groups_train_holdout = groups_full.iloc[train_idx]
groups_val_holdout = groups_full.iloc[val_idx]

print(f" Hold-out set created:")
print(f" - Train set size: {X_train_holdout.shape[0]} samples ({groups_train_holdout.nunique()} subjects)")
print(f" - Val set size: {X_val_holdout.shape[0]} samples ({groups_val_holdout.nunique()} subjects)")
print("Hold-out split complete.")

Splitting data into a single train/validation set for rapid tuning...
 Hold-out set created:
 - Train set size: 6623 samples (65 subjects)
 - Val set size: 1528 samples (16 subjects)
Hold-out split complete.


In [14]:
def create_competition_scorer(inv_map, seq_type_map):
    """
    This factory function creates a robust, self-contained scorer
    that can handle both predicted probabilities (2D) and predicted labels (1D).
    """
    def competition_f1_score_internal(y_true_encoded, y_pred, **kwargs):
        """
        The actual scoring logic. It checks the dimension of y_pred to
        determine if it needs to perform an argmax operation.
        """
        # --- ROBUSTNESS FIX ---
        if y_pred.ndim == 2:
            # Input is probabilities, find the most likely class
            y_pred_encoded = np.argmax(y_pred, axis=1)
        else:
            # Input is already encoded labels
            y_pred_encoded = y_pred

        # Map integer-encoded labels back to their string representations
        y_true_str = pd.Series(y_true_encoded).map(inv_map)
        y_pred_str = pd.Series(y_pred_encoded).map(inv_map)

        # --- The rest of the scoring logic is the same ---
        y_true_binary = y_true_str.map(seq_type_map)
        y_pred_binary = y_pred_str.map(seq_type_map)
        binary_f1 = f1_score(y_true_binary, y_pred_binary, pos_label='Target', average='binary', zero_division=0)

        def collapse_non_target(gesture):
            return 'non_target' if seq_type_map.get(gesture) == 'Non-Target' else gesture

        y_true_collapsed = y_true_str.apply(collapse_non_target)
        y_pred_collapsed = y_pred_str.apply(collapse_non_target)
        macro_f1 = f1_score(y_true_collapsed, y_pred_collapsed, average='macro', zero_division=0)

        final_score = (binary_f1 + macro_f1) / 2
        return final_score

    return competition_f1_score_internal

In [15]:
scorer_func = create_competition_scorer(inv_gesture_map, gesture_to_seq_type_map)

In [16]:
# --- Define the Robust Objective Function for Optuna ---

def objective_holdout(trial, X_train, y_train, X_val, y_val, scorer_func, seed=SEED):
    """
    Objective function for Optuna to optimize CatBoost hyperparameters.
    Uses a SINGLE, FIXED hold-out validation set for evaluation for speed.
    """
    print(f"\n--- Starting Trial: {trial.number} ---")

    # 1. Suggest hyperparameters for CatBoost
    # Focus on key parameters that significantly impact performance and training speed
    params = {
        'iterations': 1000, # Fixed, rely on early stopping
        'learning_rate': trial.suggest_float('learning_rate', 0.01, 0.3, log=True),
        'depth': trial.suggest_int('depth', 3, 8),
        'l2_leaf_reg': trial.suggest_float('l2_leaf_reg', 1.0, 10.0, log=True),
        'loss_function': 'MultiClass',
        'eval_metric': 'MultiClass',
        'random_seed': seed,
        'verbose': 0,
        'allow_writing_files': False,
        'task_type': "GPU",
        'devices': '0',
        'gpu_ram_part': 0.90, # Limit GPU RAM usage if needed to prevent crashes
    }
    print(f" - Suggested parameters: { {k:v for k,v in params.items() if k not in ['loss_function', 'eval_metric', 'random_seed', 'verbose', 'allow_writing_files']} }")

    # 2. Train CatBoost Model on the Hold-Out Training Set
    model = cat.CatBoostClassifier(**params)

    try:
        # Fit model with early stopping on the fixed validation set
        model.fit(
            X_train, y_train,
            eval_set=(X_val, y_val), # Pass the fixed hold-out validation set
            early_stopping_rounds=100, # Stop if no improvement on val set
            use_best_model=True # Use the best model found during training
        )
    except Exception as e:
        print(f" - ERROR during model.fit: {e}")
        # Returning a very low score signals failure to Optuna
        return -np.inf

    # 3. Predict and Score on the Hold-Out Validation Set
    try:
        # Use predict_proba for the competition scorer
        y_pred_proba_val = model.predict_proba(X_val)
        # Score using the provided scorer function
        val_score = scorer_func(y_val, y_pred_proba_val)
        print(f" - Trial {trial.number} Hold-Out F1 Score: {val_score:.5f}")
    except Exception as e:
        print(f" - ERROR during prediction/scoring: {e}")
        return -np.inf # Signal failure

    print(f"--- Completed Trial: {trial.number} ---\n")
    return val_score # Return the score from the single hold-out set



def run_hyperparameter_tuning_holdout(X_train, y_train, X_val, y_val, scorer_func, n_trials=N_TRIALS, seed=SEED):
    """
    Executes the Optuna hyperparameter tuning study using a hold-out validation set.
    """
    print("="*60)
    print("Starting Optuna Hyperparameter Tuning for CatBoost (Hold-Out Strategy)")
    print(f" - Training set size: {X_train.shape[0]} samples")
    print(f" - Validation set size: {X_val.shape[0]} samples")
    print(f" - Number of trials: {n_trials}")
    print(f" - Random seed: {seed}")
    print("="*60)

    # Create the Optuna study object
    study = optuna.create_study(
        direction='maximize', # We want to maximize the F1 score
        sampler=optuna.samplers.TPESampler(seed=seed), # Tree-structured Parzen Estimator
        pruner=optuna.pruners.MedianPruner() # Prune unpromising trials (optional but good)
    )

    # Create a new function that has X_train, y_train, X_val, y_val, scorer_func pre-filled
    objective_with_data = partial(objective_holdout, X_train=X_train, y_train=y_train,
                                  X_val=X_val, y_val=y_val, scorer_func=scorer_func, seed=seed)

    # Start the optimization process
    start_time = time.time()
    try:
        study.optimize(objective_with_data, n_trials=n_trials, show_progress_bar=True)
    except KeyboardInterrupt:
        print("\nOptimization interrupted by user.")
    except Exception as e:
        print(f"\nOptimization failed with error: {e}")
        raise e # Re-raise to see full traceback in notebook
    finally:
        end_time = time.time()
        elapsed_time = end_time - start_time
        print(f"\nOptimization completed in {elapsed_time/60:.2f} minutes ({elapsed_time/3600:.2f} hours).")

    # --- Print and Log the Best Results ---
    print("\n" + "="*60)
    print("Optuna Hyperparameter Tuning Complete (Hold-Out)")
    print("="*60)
    print(f"Number of finished trials: {len(study.trials)}")

    if study.best_trial:
        best_trial = study.best_trial
        print(f"Best trial's Hold-Out F1 Score: {best_trial.value:.5f}")
        print("Best trial's hyperparameters:")
        for key, value in best_trial.params.items():
            print(f" {key}: {value}")

        # Optional: Save the study for analysis
        study.trials_dataframe().to_csv('optuna_catboost_holdout_trials.csv', index=False)
        print("Study trials saved to 'optuna_catboost_holdout_trials.csv'")

        return study
    else:
        print("No successful trials completed.")
        return None

In [17]:
study = run_hyperparameter_tuning_holdout(X_train_holdout, y_train_holdout, X_val_holdout,
                                         y_val_holdout, scorer_func, n_trials=N_TRIALS, seed=SEED)

[I 2025-09-02 09:23:32,687] A new study created in memory with name: no-name-39485a11-778b-495f-987e-7cd75d3ce1a4


Starting Optuna Hyperparameter Tuning for CatBoost (Hold-Out Strategy)
 - Training set size: 6623 samples
 - Validation set size: 1528 samples
 - Number of trials: 75
 - Random seed: 42


  0%|          | 0/75 [00:00<?, ?it/s]


--- Starting Trial: 0 ---
 - Suggested parameters: {'iterations': 1000, 'learning_rate': 0.03574712922600244, 'depth': 8, 'l2_leaf_reg': 5.395030966670228, 'task_type': 'GPU', 'devices': '0', 'gpu_ram_part': 0.9}
 - Trial 0 Hold-Out F1 Score: 0.83653
--- Completed Trial: 0 ---

[I 2025-09-02 09:31:08,159] Trial 0 finished with value: 0.8365289628298885 and parameters: {'learning_rate': 0.03574712922600244, 'depth': 8, 'l2_leaf_reg': 5.395030966670228}. Best is trial 0 with value: 0.8365289628298885.

--- Starting Trial: 1 ---
 - Suggested parameters: {'iterations': 1000, 'learning_rate': 0.07661100707771368, 'depth': 3, 'l2_leaf_reg': 1.4321698289111515, 'task_type': 'GPU', 'devices': '0', 'gpu_ram_part': 0.9}
 - Trial 1 Hold-Out F1 Score: 0.82377
--- Completed Trial: 1 ---

[I 2025-09-02 09:31:30,868] Trial 1 finished with value: 0.8237705236769453 and parameters: {'learning_rate': 0.07661100707771368, 'depth': 3, 'l2_leaf_reg': 1.4321698289111515}. Best is trial 0 with value: 0.8365

In [18]:
if 'study' in locals() and study is not None:
    # Save the study for analysis
    print("Best Parameters:", study.best_params)
    print("Best Value:", study.best_value)
    optuna.visualization.plot_optimization_history(study)
    optuna.visualization.plot_param_importances(study)

Best Parameters: {'learning_rate': 0.08579514753476217, 'depth': 8, 'l2_leaf_reg': 1.1367839827002824}
Best Value: 0.8488733260706264


## Validation Step

In [19]:
def validate_best_params_cv(X_full, y_full, groups_full, best_params, scorer_func, n_splits=5, seed=SEED):
  print("Validating best parameters on full dataset using cross-validation...")
  cv = StratifiedGroupKFold(n_splits=n_splits, shuffle=True, random_state=seed)
  fold_scores =[]

  for fold, (train_idx, val_idx) in enumerate(cv.split(X_full, y_full, groups_full)):
    print(f" --- Fold {fold+1}/{n_splits} ---")
    X_train_fold, y_train_fold = X_full.iloc[train_idx], y_full.iloc[train_idx]
    X_val_fold, y_val_fold = X_full.iloc[val_idx], y_full.iloc[val_idx]

    model = cat.CatBoostClassifier(**best_params)
    model.fit(X_train_fold, y_train_fold, eval_set=(X_val_fold, y_val_fold),
              early_stopping_rounds=100, use_best_model=True, verbose=0)

    y_pred_proba = model.predict_proba(X_val_fold)
    score = scorer_func(y_val_fold, y_pred_proba)
    fold_scores.append(score)
    print(f" - Fold {fold+1} F1 Score: {score:.5f}")

  mean_score = np.mean(fold_scores)
  std_score = np.std(fold_scores)
  print(f"\nFinal CV Score with best params: {mean_score:.5f} (+/- {std_score:.5f})")
  return mean_score, std_score


In [ ]:
if 'study' in locals() and study is not None:
  best_params = study.best_trial.params
  # Fixed params
  best_params['iterations'] = 1000
  best_params['loss_function'] = 'MultiClass'
  best_params['eval_metric'] = 'MultiClass'
  best_params['random_seed'] = SEED
  best_params['verbose'] = 0
  best_params['allow_writing_files'] = False
  best_params['task_type'] = 'GPU'
  best_params['devices'] = '0'
  best_params['gpu_ram_part'] = 0.90

  final_mean, final_std = validate_best_params_cv(X_full, y_full, groups_full, best_params, scorer_func, n_splits=5, seed=SEED)
  print(f"Final CV Mean Score: {final_mean:.5f} (+/- {final_std:.5f})")


Validating best parameters on full dataset using cross-validation...
 --- Fold 1/5 ---
 - Fold 1 F1 Score: 0.84887
 --- Fold 2/5 ---
 - Fold 2 F1 Score: 0.79455
 --- Fold 3/5 ---
 - Fold 3 F1 Score: 0.77383
 --- Fold 4/5 ---
